In [1]:
import pandas as pd
from edastatmil_milser import edas_tatmil as EDA
from szip_engine import compress_and_split, decompress_volumes
pd.set_option('display.max_rows', None)

## 1. Stars sample preview

In [2]:
df = pd.read_csv('../Samples/Clusters.csv')
df.head()

_Glon      _Glat   _RAJ2000   _DEJ2000 Cluster
0  136.163369 -23.291857  28.329417  37.984833   Mel12
1  136.390938 -23.836403  28.405333  37.404806   Mel12
2  136.386537 -23.211326  28.607250  38.009139   Mel12
3  136.553405 -23.705483  28.629333  37.492111   Mel12
4  136.587727 -23.750297  28.652583  37.440583   Mel12

In [3]:
df.shape

(992227, 5)

Obtenemos una lista de los numbres de los clusters incluidos en el stars sample

In [4]:
actual_name = df['Cluster'].unique()
actual_name

array(['Mel12', 'Mel25', 'NGC 2632', 'NGC 2168', 'NGC 2099', 'NGC 1746',
       'NGC 1039', 'NGC 1647', 'NGC 2183', 'NGC 1912', 'NGC 2281',
       'NGC 2420', 'NGC 2158', 'NGC 869', 'NGC 1662', 'Basel 11B',
       'NGC 1528', 'NGC 2252', 'Basel 4', 'NGC 1960', 'NGC 6205',
       'Waterloo 2', 'NGC 6819', 'NGC 5272', 'Berkeley 71', 'Berkeley 32',
       'Berkeley 17', 'Berkeley 29', 'Berkeley 53', 'Berkeley 66',
       'FSR 0494', 'IC 166', 'King 5', 'King 7', 'M 107', 'M 13', 'M 15',
       'M 2', 'M 3', 'M 35', 'M 5', 'M 53', 'M 67', 'M 71', 'M 92',
       'NGC 1245', 'NGC 1798', 'NGC 188', 'NGC 2243', 'NGC 2682',
       'NGC 4147', 'NGC 5466', 'NGC 6791', 'NGC 6811', 'NGC 7789',
       'Pleiades', 'Teutsch 51', 'Mel13', 'Mel14', 'NGC 2532', 'IC 2395',
       'NGC 2808', 'NGC 0104', 'NGC 1904', 'NGC 1851', 'NGC 6266',
       'NGC 5139', 'NGC 3201', 'NGC 0362', 'NGC 5286', 'NGC 6218',
       'NGC 5904', 'NGC 6093', 'NGC 6254', 'NGC 6293', 'NGC 6388',
       'NGC 6522', 'NGC 6441', 'NGC

Hay que comprobar que no tenemos el mismo cluster nombrado de dos formas diferentes. Para ello:
1. Vamos a hacer un dataframe con los diferentes nombres de los clusters los diferentes catálogos posibles.
2. Escogeremos el catálogo con el que vamos a trabajar para tener todos los cluster identificados bajo un mismo criterio.
3. Renombraremos los clusters con el nombre escogido.

### 1.1 Rename clusters
Se hace una lista para los nombres en cada catalogo, basada en la lista de nombres de clusters obtenida del stars sample. Si un nombre de la lista inicial no está en algún catálogo, agregamos None.

In [5]:
NGC_names = ['NGC752', None, 'NGC 2632', 'NGC 2168', 'NGC 2099', 'NGC 1746', 'NGC 1039','NGC 1647','NGC 2183','NGC 1912', 'NGC 2281', 'NGC 2420', 'NGC 2158','NGC 869','NGC 1662', None,'NGC 1528','NGC 2252', None,'NGC 1960', 'NGC 6205', None, 'NGC 6819','NGC 5272', None, None, None, None, None, None, None, None, None, None, 'NGC 6171', 'NGC 6205','NGC 7078', 'NGC 7089', 'NGC 5272',' NGC 2168', 'NGC 5904','NGC 5024','NGC 2682','NGC 6838','NGC 6341','NGC 5145','NGC 1798','NGC 188','NGC 2243','NGC 2682','NGC 4147','NGC 5466','NGC 6791','NGC 6811','NGC 7789', None, None,'NGC 869', 'NGC 884','NGC 2532', None, 'NGC 2808','NGC 0104','NGC 1904','NGC 1851','NGC 6266', 'NGC 5139','NGC 3201','NGC 0362','NGC 5286', 'NGC 6218', 'NGC 5904', 'NGC 6093', 'NGC 6254', 'NGC 6293', 'NGC 6388','NGC 6522', 'NGC 6441', 'NGC 6541','NGC 6624','NGC 7078','NGC 6656','NGC 6681','NGC 6752','NGC 7089','NGC 7099', None, None, None,'NGC 457','NGC 884','NGC 1502','NGC 2244', 'NGC 2362','NGC 2384','NGC 2422','NGC 2467','NGC 3293','NGC 4755','NGC 6193','NGC 7160', None, None, None,'NGC 1261','NGC 3201','NGC 6139','NGC 6205','NGC 6362','NGC 6397','NGC 6712', None]
Mel_names = ['Mel 12', 'Mel 25', 'Mel 88', None, None, None, None, None, None, None, None, 'Mel 69', 'Mel 40', 'Mel 13', None, None, None, None, None, None, None, None, 'Mel 223', 'Mel 119', None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, 'Mel 18', None, 'Mel 2','Mel 46', None, None, None, None, 'Mel 222', 'Mel 245', 'Mel 22', None, 'Mel 13', 'Mel 14', None, None, None, 'Mel 1', None, None, None, None, None, 'Mel 4', None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, 'Mel 15', None, None, 'Mel 14', None, None, None, None, None, None,'Mel 100','Mel 144', None, None, None, None, None, None, None, None, None, None, None, None, None]
M_names = [None, None, 'M 44', 'M 35', 'M 37', None, 'M 34',None, None, 'M 38', None, None, None, None, None, None, None, None, None, 'M 36', 'M 13', None, None, 'M 3', None, None, None, None, None, None, None, None, None, None, 'M 107', 'M 13','M 15','M 2', 'M 3','M 35','M 5', 'M 53', 'M 67', 'M 71', 'M 92', None, None, None, None, 'M 67', None, None, None, None, None,'M 45', None, None, None, None, None, None, None, 'M 79', None, 'M 62', None, None, None, None, 'M 12', 'M 5', 'M 80', 'M 10', None, None, None, None, None, None,'M 15', 'M 22','M 70', None,'M 2','M 30', None, None, None, None, None, None, None, None, None, 'M 47', None, None, None, None, None, None, None, None, None, None, None, 'M 13', None, None, None, None]
Common_name = [None, 'Hiades', 'Beehive', None, None, None, None, None, None, None, None, None, None, 'H Persei', None, 'Basel 11b', None, None, None, None,'Hercules', None, 'Foxhead', None, None, None, None, None, None, None, None, None, None, None, None, 'Hercules', None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, 'Pleiades', None, 'H Persei', 'Chi Persei', None, None, None, '47 Tuc', None, None, None, 'Ome Cen', None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, 'AFGL 333', 'lam Cen','ET','Chi Persei', None, None, 'Tau CMa', None, None, None, None,'Jewel Box', None, None, None, None, None, None, None, None,'Hercules', None, None, None, None]

Comprobamos que la longitud de todas las listas es la misma, de forma que no nos hemos equivocado. Si todo está bien, construimos el dataframe de la tabla de equivalencia de nombres.

In [6]:
print(len(actual_name))
print(len(NGC_names))
print(len(Mel_names))
print(len(M_names))
print(len(Common_name))

112
112
112
112
112


In [7]:
clusters_names = pd.DataFrame(actual_name, columns=['Actual Names'])
clusters_names['NGC_names'] = NGC_names
clusters_names['Mel_names'] = Mel_names
clusters_names['M_names'] = M_names
clusters_names['Common_name'] = Common_name
clusters_names.head(5)

Actual Names NGC_names Mel_names M_names Common_name
0        Mel12    NGC752    Mel 12    None        None
1        Mel25      None    Mel 25    None      Hiades
2     NGC 2632  NGC 2632    Mel 88    M 44     Beehive
3     NGC 2168  NGC 2168      None    M 35        None
4     NGC 2099  NGC 2099      None    M 37        None

Eliminamos los espacios de los nombres

In [8]:
def remove_spaces(x):
    if isinstance(x, str):
        return x.replace(' ', '').strip()
    return x

cluster_cols = clusters_names.columns.tolist()

for col in cluster_cols:
    clusters_names[col] = clusters_names[col].apply(remove_spaces)
clusters_names.head(5)

Actual Names NGC_names Mel_names M_names Common_name
0        Mel12    NGC752     Mel12    None        None
1        Mel25      None     Mel25    None      Hiades
2      NGC2632   NGC2632     Mel88     M44     Beehive
3      NGC2168   NGC2168      None     M35        None
4      NGC2099   NGC2099      None     M37        None

Eliminamos las filas repetidas usando la columna NGC_names, ya que es donde más nombres encontramos. Hay que tener en cuenta que no se aplique la eliminación de duplicados a las filas donde NGC_names sea None

In [9]:
# Filtrar filas que no sean None en 'NGC_names'
filtered_clusters = clusters_names[clusters_names['NGC_names'].notna()]

# Eliminar duplicados en las filas filtradas
filtered_clusters = filtered_clusters.drop_duplicates(subset='NGC_names')

# Filtrar filas que sean None en 'NGC_names'
none_clusters = clusters_names[clusters_names['NGC_names'].isna()]

# Concatenar las filas filtradas sin duplicados y las filas con None
Name_equival = pd.concat([filtered_clusters, none_clusters], ignore_index=True)

Name_equival.head(5)

Actual Names NGC_names Mel_names M_names Common_name
0        Mel12    NGC752     Mel12    None        None
1      NGC2632   NGC2632     Mel88     M44     Beehive
2      NGC2168   NGC2168      None     M35        None
3      NGC2099   NGC2099      None     M37        None
4      NGC1746   NGC1746      None    None        None

In [10]:
Name_equival.to_csv('../Samples/Clean/NamesCatalogEquivalence.csv')

Trabajaremos siempre que sea posible con el NGC_name. En los casos en los que no tenemos NGC_name, se trabajará con el Actual Name.Entonces:
1. Tanto en la columna Cluster del dataset como en las columnas de la tabla clusters_names, eliminaremos los espacios.
2. Recorremos el dataset de estrellas y allá donde la columna Cluster no tiene el nombre NGC, lo tomaremos de la tabla de equivalencia de nombres y lo sustituiremos. Si no hay un nombre NGC, dejamos el que está.

In [11]:
df['Cluster'] = df['Cluster'].str.replace(r'\s+', '', regex=True).str.strip()

In [12]:
def rename(name):
    if 'NGC' in name:
        return name
    else:
        row = clusters_names.index[clusters_names['Actual Names'] == name]
        if not row.empty and clusters_names.at[row[0], 'NGC_names'] is not None:
            return clusters_names.at[row[0], 'NGC_names']
        else:
            return name

df['Cluster'] = df['Cluster'].apply(rename)
actual_name = df['Cluster'].unique()
actual_name

array(['NGC752', 'Mel25', 'NGC2632', 'NGC2168', 'NGC2099', 'NGC1746',
       'NGC1039', 'NGC1647', 'NGC2183', 'NGC1912', 'NGC2281', 'NGC2420',
       'NGC2158', 'NGC869', 'NGC1662', 'Basel11B', 'NGC1528', 'NGC2252',
       'Basel4', 'NGC1960', 'NGC6205', 'Waterloo2', 'NGC6819', 'NGC5272',
       'Berkeley71', 'Berkeley32', 'Berkeley17', 'Berkeley29',
       'Berkeley53', 'Berkeley66', 'FSR0494', 'IC166', 'King5', 'King7',
       'NGC6171', 'NGC7078', 'NGC7089', 'NGC5904', 'NGC5024', 'NGC2682',
       'NGC6838', 'NGC6341', 'NGC1245', 'NGC1798', 'NGC188', 'NGC2243',
       'NGC4147', 'NGC5466', 'NGC6791', 'NGC6811', 'NGC7789', 'Pleiades',
       'Teutsch51', 'NGC884', 'NGC2532', 'IC2395', 'NGC2808', 'NGC0104',
       'NGC1904', 'NGC1851', 'NGC6266', 'NGC5139', 'NGC3201', 'NGC0362',
       'NGC5286', 'NGC6218', 'NGC6093', 'NGC6254', 'NGC6293', 'NGC6388',
       'NGC6522', 'NGC6441', 'NGC6541', 'NGC6624', 'NGC6656', 'NGC6681',
       'NGC6752', 'NGC7099', 'Berkeley86', 'IC1805', 'IC2944', 

Además, buscando en bases de datos los nombres de los clusters, hemos visto que los clusters FSR 0494 y CR 228 no existen como clusters oficiales, así que eliminaremos las filas correspondientes a estos clusters del dataset.

In [13]:
nonfinderdlusters = ['FSR0494','CR228']
df = df.query('Cluster not in @nonfinderdlusters')

In [14]:
df.to_csv('../Samples/RenamedClusters.csv')
df.head(5)

_Glon      _Glat   _RAJ2000   _DEJ2000 Cluster
0  136.163369 -23.291857  28.329417  37.984833  NGC752
1  136.390938 -23.836403  28.405333  37.404806  NGC752
2  136.386537 -23.211326  28.607250  38.009139  NGC752
3  136.553405 -23.705483  28.629333  37.492111  NGC752
4  136.587727 -23.750297  28.652583  37.440583  NGC752

In [15]:
n,c = EDA.explore(df)

Rows: 992199
Columns: 5
+----------+----------------+------------+-----------+---------------+
|          | Non-Null Count | Null Count | Data Type | Data Category |
+----------+----------------+------------+-----------+---------------+
|  _Glon   |     992197     |     2      |  float64  |   Numerical   |
|  _Glat   |     992197     |     2      |  float64  |   Numerical   |
| _RAJ2000 |     992197     |     2      |  float64  |   Numerical   |
| _DEJ2000 |     992197     |     2      |  float64  |   Numerical   |
| Cluster  |     992199     |     0      |  object   |  Categorical  |
+----------+----------------+------------+-----------+---------------+


Ahora con este dataframe haremos un merge en la base de datos de Gaia DR3 mediante el software TopCat. Lo que hace este software es acceder a la base de datos de la misión espacial Gaia, en su versión más actualiada (DR3). Usando las coordenadas que situan a cada estrella en el cielo (_RAJ2000 y _DEJ2000 en nuestro dataset), va a buscar nuestras estrellas en la base de datos y agregar las columnas con todos los datos y características que tenga sobre ellas. El dataset resultante pesa mucho asi que esta comprimido en distintas partes. Para obtenerlo hay que descomprimirlos en la carpeta ../Samples/

In [16]:
#decompress_volumes('STARSSample', '../Samples', '../Samples/Compressed') TODO descomentar

# Alternativamente el dataset esta en esta carpeta de drive:
# https://drive.google.com/drive/folders/1ac8yV0D-KNRFOH3jnlYUnNfeU6bkZc8S

## 2. ClustersInfo explore

Este dataset contiene información general sobre el cúmulo. Es importante ya que con ella vamos a poder reemplazar información que falte en STARSSample e identificar los clusters que obtengamos.

In [17]:
clusters_info = pd.read_csv('../Samples/ClustersInfo.csv', delimiter=';')
clusters_info.head(5)

Cluster     RAJ2000   DEJ2000     GLON     GLAT  RV (km/s)  pmRA (mas/yr)  \
0   NGC 752  01 56 53.5  37 47 38  136.958   -23.28       5.44         98.092   
1     Mel25  04 29 47.3  16 56 53  179.627  -21.124      37.97        104.920   
2  NGC 2632  08 40 13.0  19 37 16  205.952   32.427      34.94        -36.047   
3  NGC 2168  06 09 05.3  24 20 10  186.609    2.230      -6.37         22.784   
4  NGC 2099  05 52 17.8  32 32 42   177.64    3.086       7.70          1.924   

   pmDE (mas/yr)  Plx (mas)  
0       -117.637     22.304  
1        -28.000     21.052  
2        -12.917      5.371  
3        -29.336     11.301  
4         -5.648    666.000

Tenemos indicativos de tabulador en algunas celdas. Limpiamos esto:

In [18]:
def remove_tabs(x):
    if isinstance(x, str):
        return x.replace('\t', '')
    return x
clusters_info = clusters_info.map(remove_tabs)
clusters_info.head(5)

Cluster     RAJ2000   DEJ2000     GLON     GLAT  RV (km/s)  pmRA (mas/yr)  \
0   NGC 752  01 56 53.5  37 47 38  136.958   -23.28       5.44         98.092   
1     Mel25  04 29 47.3  16 56 53  179.627  -21.124      37.97        104.920   
2  NGC 2632  08 40 13.0  19 37 16  205.952   32.427      34.94        -36.047   
3  NGC 2168  06 09 05.3  24 20 10  186.609    2.230      -6.37         22.784   
4  NGC 2099  05 52 17.8  32 32 42   177.64    3.086       7.70          1.924   

   pmDE (mas/yr)  Plx (mas)  
0       -117.637     22.304  
1        -28.000     21.052  
2        -12.917      5.371  
3        -29.336     11.301  
4         -5.648    666.000

Hay que hacer el mismo tratamiento para los nombres que con STARSSample:
1. Eliminar espacios
2. Sustituir por los nombres que hemos dejado en STARSSample

In [19]:
clusters_info['Cluster'] = clusters_info['Cluster'].str.replace(r'\s+', '', regex=True).str.strip()

In [20]:
clusters_info['Cluster'] = clusters_info['Cluster'].apply(rename)
clusters_info.head(5)

Cluster     RAJ2000   DEJ2000     GLON     GLAT  RV (km/s)  pmRA (mas/yr)  \
0   NGC752  01 56 53.5  37 47 38  136.958   -23.28       5.44         98.092   
1    Mel25  04 29 47.3  16 56 53  179.627  -21.124      37.97        104.920   
2  NGC2632  08 40 13.0  19 37 16  205.952   32.427      34.94        -36.047   
3  NGC2168  06 09 05.3  24 20 10  186.609    2.230      -6.37         22.784   
4  NGC2099  05 52 17.8  32 32 42   177.64    3.086       7.70          1.924   

   pmDE (mas/yr)  Plx (mas)  
0       -117.637     22.304  
1        -28.000     21.052  
2        -12.917      5.371  
3        -29.336     11.301  
4         -5.648    666.000

In [21]:
clusters_info.to_csv('../Samples/Clean/ClustersInfo_clean.csv')

## 3. STARSSample explore

In [22]:
stars_df = pd.read_csv('../Samples/STARSSample.csv')
num, cat = EDA.explore(stars_df)
print('no quiero verlo')

Rows: 984102
Columns: 134
+----------------+----------------+------------+-----------+---------------+
|                | Non-Null Count | Null Count | Data Type | Data Category |
+----------------+----------------+------------+-----------+---------------+
|      col1      |     984102     |     0      |   int64   |   Numerical   |
|     _Glon      |     984102     |     0      |  float64  |   Numerical   |
|     _Glat      |     984102     |     0      |  float64  |   Numerical   |
|    _RAJ2000    |     984102     |     0      |  float64  |   Numerical   |
|    _DEJ2000    |     984102     |     0      |  float64  |   Numerical   |
|    Cluster     |     984102     |     0      |  object   |  Categorical  |
|    DR3Name     |     984102     |     0      |  object   |  Categorical  |
|     RAdeg      |     984102     |     0      |  float64  |   Numerical   |
|     DEdeg      |     984102     |     0      |  float64  |   Numerical   |
|   errHalfMaj   |     984102     |     0      |  

Definición de las columnas:
- col1: índice
- _Glon: coordenada longitud galáctica. Ángulo sobre el disco de la galaxia desde la dirección del centro galáctico hasta la vertical de la estrella.
- _Glat: coordenada latitud galáctica. Ángulo desde el disco galactico hasta la estrella.
- _RAJ2000: coordenada ascensión recta de la época 2000. Ángulo sobre el ecuador desde el punto vernal hasta la vertical de la estrella.
- _DEJ2000: coordenada declinación de la época 2000. Ángulo desde el ecuador hasta la estrella.
- Cluster: Nombre del cúmulo al que pertenece la estrella.
- DR3Name: Nombre de la estrella en el catálogo DR3 de Gaia.
- RAdeg: igual que _RAJ2000
- DEdeg: igual que _DEJ2000
- *errHalfMaj, *errHalfMin, *errPosAng: errores de la medida de la posición.
- *SolID, *Source, *RandomI: otros identificadores.
- e_RAdeg, e_DEdeg: errores en la medida de ascensión recta y declinación.
- Plx: paralaje. Es el dato que necesitamos para obtener la distancia.
- e_Plx: error en la medida del paralaje.
- RPlx: paralaje dividido por su desviación estándar.
- PM: movimiento propio.
- pmRA: velocidad de la estrella en su movimiento propio respecto al centro de la galaxia en la coordenada ascensión recta. Medido en mas/yr.
- e_pmRA: error en la medida de pmRA.
- pmDE: velocidad de la estrella en su movimiento propio respecto al centro de la galaxia en la coordenada declinación. Medido en mas/yr.
- e_pmDE: error en la medida de pmDE.
- RADEcor, RAPlxcor,RApmRAcor,RApmDEcor, DEPlxcor, DEpmRAcor,DEpmDEcor, PlxpmRAcor,PlxpmDEcor, pmRApmDEcor: correlaciones entre magnitudes.
- NAL, NAC: número total de observaciones en diferentes longitudes de onda.
- NgAL, NgAL: número de buenas observaciones en diferentes longitudes de onda.
- *gofAL, *chi2AL: estádisticas de la bondad de las observaciones.
- epsi, sepsi: exceso de ruido en la observación de la fuente y su significancia.
- *Solved: parámetros astrométricos resueltos.
- *APF: astrometría primaria o secundaria.
- *nueff: número de onda efectivo usado en la solución astrométrica.
- pscol: pseudocolor estimado astrométricamente.
- e_pscol: error en la medida de pscol.
- RApscolCorr, DEpscolCorr, PlxpscolCorr,pmRApscolCorr,pmDEpscolCorr: correlaciones entre las variables.
- *MatchObsA: tránsitos encontrados en FOV usando la solución AGIS.
- Nper: número de periodos de visibilidad usados en la solución astrométrica.
- amax: eje semimayor del elipsoide de error.
- *IPDgofha: amplitud del GoF IPD.
- MatchObs: número total de tránsitos.
- *IPDgofhp: fase del GoF IPD.
- *IPDfmp: porcentaje de éxito de la ventana IPD.
- *IPDfow: porcentaje de tránsitos fallidos.
- RUWE: error de peso normalizado.
- *Dup: si es una fuente con múltiples identificadores.
- o_Gmag: número de tránsitos que contibuyen a la medida del flujo en Gmag.
- FG: flujo medio en la banda G.
- e_FG: error de FG.
- RFG: FG dividido por su error.
- Gmag: magnitud en la banda G.
- e_Gmag: error de Gmag.
- o_BPmag: numero de observaciones que contribuye a fotometría BP.
- FBP: flujo medio en la banda BP.
- e_FBP: error de FBP.
- RFBP: FBP dividido por su error.
- BPmag: magnitud en la banda BP.
- e_BPmag: error de BPmag.
- o_RPmag: numero de tránsitos que contribuye a la fotometría RP.
- FRP: flujo medio en la banda RP.
- e_FRP: error de FRP.
- RFRP: FRP dividido por su error.
- RPmag: magnitud en la banda RP.
- e_RPmag: error de RPmag.
- E(BP/RP): factor de exceso de color en BP/RP.
- NBPcont, NRPcont: numero de tránsitos contaminados en cada banda.
- NBPblend, NRPblend: número de tránsitos mezclados en cada banda.
- *Mode: modo de procesamiento de la fotometría.
- BP-RP, BP-G,G-RP: colores en diferentes bandas.
- RV: velocidad radial.
- e_RV: error de la velocidad radial.
- *n_RV: método usado para obtener la velocidad radial.
- o_RV: número de tránsitos usados para obtener la velocidad radial.
- o_RVd: número de tránsitos válidos.
- RVNper: número de periodos de visibilidad usados para obtener la velocidad radial.
- RVS/N: ratio de ruido en la señal espectral para obtener la velocidad radial.
- *RVgof, *RVchi2: estadísticas en el cálculo de RV.
- *RVTdur: tiempo cubierto en la serie temporal de velocidad radial.
- *RVamp: amplitud máxima en la serie temporal de velocidad una vez eliminados los outliers.
- RVtempTeff: temperatura efectiva del modelo usado para calcular la velocidad radial.
- RVtemplogg: logaritmo de la temperatura efectiva.
- RVtemp[Fe/H]: metalicidad del modelo usado para calcular la temperatura efectiva.
- Vatmparam: origen de los parámetros atmoféricos asociados al modelo.
- vbroad: líneas espectrales ampliadas.
- e_Vbroad: error de vbroad.
- o_Vbroad: número de tránsitos usados para calcular vbroad.
- GRVSmag: magnitud Grvs.
- e_GRVSmag: error de GRVSmag.
- o_GRVSmag: número de tránsitos usados para calcular o_GRVSmag.
- RVSS/N: ratio de señal/ruido en el espectro de RVS.
- *VarFlag: marcador de variabilidad fotométrica.
- PQSO: probabilidad de que sea un quásar.
- PGal: probabilidad de que sea una galaxia.
- PSS: probabilidad de que sea una única estrella.
- Teff: temperatura efectiva con la banda BP/RP.
- logg: gravedad en la superficie de la estrella con la banda BP/RP
- \[Fe/H]: metalicidad
- Dist: distancia usando la banda BP/RP.
- A0: extinción.
- AG: extinción en la banda G.
- E(BP-RP): enrojecimiento en la banda BP-RP.
- *Lib: nombre de la librería usada en parámetros de astrofotometría.
- RAJ2000: igual que _RAJ2000
- DEJ2000: igual que _DEJ2000
- e_RAJ2000: error de RAJ2000
- e_DEJ2000: error deDEJ2000
- RADEcorj2000: corrección de época J2000
- angDist: distancia angular.
- *CartessianCoord: vector con las coordenadas cartesianas x,y,z
- X: coordenada cartesiana x
- Y: coordenada cartesiana y
- Z: coordenada cartesiana z
  
> Nuestro target es la columna Clusters y el resto son variables predictoras

### 2.1 Eliminación de las columnas repetidas


In [23]:
stars_df_clean = stars_df.drop(columns=['RAdeg','DEdeg','RAJ2000','DEJ2000'])

### 2.2 Eliminación de información irrelevante


In [24]:
stars_df_clean = stars_df_clean.drop(columns=['errHalfMaj', 'errHalfMin', 'errPosAng', 'SolID', 'Source', 'RandomI', 'gofAL', 'chi2AL', 'Solved', 'APF', 'nueff', 'MatchObsA', 'IPDgofha', 'IPDgofhp', 'IPDfmp', 'IPDfow', 'Dup', 'Mode', 'n_RV', 'RVgof', 'RVchi2', 'RVTdur', 'RVamp', 'VarFlag', 'Lib', 'CartesianCoord'])

### 2.3 Tratamiento de valores nulos
Parece haber muchas estrellas sin la variable Plx, por lo que no podemos calcular la distancia para ellas. Habrá que valorar si se eliminan estos objetos o si se sustituye Plx por el Plx que hay en la tabla ClustersInfo para los cúmulos a los que pertenezcan las estrellas.

Hay que hacer una exploración más a fondo para ver si tenemos valores nulos en más columnas.

In [25]:

pd.set_option('display.max_rows', None)

nulos_por_cluster = stars_df_clean.groupby('Cluster')['Plx'].apply(lambda x: x.isnull().sum())
nulos_por_cluster_total = stars_df_clean.groupby('Cluster').size()
nulos_por_cluster_nulos = nulos_por_cluster[nulos_por_cluster > 0]

df_t = nulos_por_cluster_total.reset_index()
df_n = nulos_por_cluster_nulos.reset_index()

df_t.columns = ['Cluster', 'nulos_t']
df_n.columns = ['Cluster', 'nulos_n']

df_merged = pd.merge(df_t, df_n, on='Cluster',how='inner',validate='1:1')

df_merged['n_percentage'] = df_merged.apply(lambda row: 100* row['nulos_n'] / row['nulos_t'] if row['nulos_t'] != 0 else float('inf'), axis=1)
df_merged_sorted = df_merged.sort_values(by='n_percentage', ascending=False)




In [26]:
# Seleccionar las filas de df_merged_sorted donde 'n_percentage' es mayor que 50
# y 'Plx' es nulo TODO
#rows_to_drop = df_merged_sorted.loc[(df_merged_sorted['n_percentage'] > 50) , 'Cluster']# & stars_df_clean['Plx'].isna()
# Eliminar las filas del DataFrame stars_df_clean basadas en las filas seleccionadas
#stars_df_clean = stars_df_clean.drop(stars_df_clean[(stars_df_clean['Cluster'].isin(rows_to_drop)) & (stars_df_clean['Plx'].isnull())].index)



### 2.4 Limpieza general de datos
Las variables PQSO y PGal nos dan las probabilidad que estima el satélite de que ese objeto sea en realidad una galaxia lejana o un quásar en lugar de una estrella. Hay que hacer un histograma de estas variables y decidir a partir de qué probabilidades eliminamos el objeto (por ejemplo, todo lo que sea por encima de 80% de probabilidad de ser algo que no es una estrella??).

In [27]:
#Detectamos las columnas que tienen un porcentaje elevado de nulos respecto al total de datos en esa columna.

n_pc = 60 #%

total_values_per_column = stars_df_clean.shape[0]
# Calculate the number of null values in each column
null_values_per_column = stars_df_clean.isnull().sum()
# Calculate the percentage of null values in each column
percentage_null_per_column = (null_values_per_column / total_values_per_column) * 100

percentage_null_per_column.sort_values(ascending=False)

cols_to_drop_nul_pc = percentage_null_per_column[percentage_null_per_column>n_pc]


In [28]:
#PQSO y PGal
#Podemos quitarlas, representan un 1% del dataset

print(stars_df_clean[stars_df_clean['PQSO'] > 0.05])
print(stars_df_clean[stars_df_clean['PGal'] > 0.05])


          col1       _Glon      _Glat    _RAJ2000   _DEJ2000     Cluster  \
3985     17261  282.189172 -11.237250  138.033750 -64.850412     NGC2808   
4947     10761  282.180718 -11.251386  137.995988 -64.853739     NGC2808   
4977     10793  282.181512 -11.261733  137.979143 -64.861251     NGC2808   
5260       356  203.144798  37.535219  134.460290  23.439175     NGC2632   
7424     15439  244.496057 -35.038639   78.522190 -40.033002     NGC1851   
7614     15636  227.233315 -29.352969   81.043890 -24.528160     NGC1904   
8489     11374  282.186809 -11.238316  138.028232 -64.849407     NGC2808   
8688     11593  282.189172 -11.237250  138.033750 -64.850412     NGC2808   
10629    14588  244.524766 -35.037673   78.527681 -40.056149     NGC1851   
10806    14781  244.527644 -35.043540   78.520514 -40.059293     NGC1851   
10922    14898  244.512350 -35.021307   78.547020 -40.043818     NGC1851   
11779     3960  215.640128  31.800066  132.715458  11.802833     NGC2682   
12101    196

### 2.5 Factorización de variables categóricas y target
Se factorizan las variables categóricas y se guarda la tabla de equivalencia.

In [29]:
cat, num = EDA.explore(stars_df_clean)
EDA.factorize_categorical(stars_df_clean,cat)

Rows: 984102
Columns: 104
+---------------+----------------+------------+-----------+---------------+
|               | Non-Null Count | Null Count | Data Type | Data Category |
+---------------+----------------+------------+-----------+---------------+
|     col1      |     984102     |     0      |   int64   |   Numerical   |
|     _Glon     |     984102     |     0      |  float64  |   Numerical   |
|     _Glat     |     984102     |     0      |  float64  |   Numerical   |
|   _RAJ2000    |     984102     |     0      |  float64  |   Numerical   |
|   _DEJ2000    |     984102     |     0      |  float64  |   Numerical   |
|    Cluster    |     984102     |     0      |  object   |  Categorical  |
|    DR3Name    |     984102     |     0      |  object   |  Categorical  |
|    e_RAdeg    |     984102     |     0      |  float64  |   Numerical   |
|    e_DEdeg    |     984102     |     0      |  float64  |   Numerical   |
|      Plx      |     867897     |   116205   |  float64  |   

KeyboardInterrupt: 

### El sample resultado de estos cambios se guarda como '../Samples/PostEDA/STARS_PreCleaned.csv'
### Las tablas de equivalencia de las categóricas se guarda como '../Samples/Auxiliar/NombreVariable_Factorization.csv'